In [1]:
import pandas as pd

In [5]:
from tms_data_interface import SQLQueryInterface
seq = SQLQueryInterface(schema="transactionschema")

In [6]:
seq.execute_raw("show tables")

[['account_data_v1'],
 ['account_data_v2'],
 ['alert_data_v1'],
 ['alert_data_v2'],
 ['customer_data_v1'],
 ['customer_data_v2'],
 ['transaction10m'],
 ['transaction60m']]

In [7]:
query = """
    select  final.CUSTOMER_NUMBER_main as Focal_id,
            final.Credit_transaction_amount,
            final.Total_no_of_credit_transactions,
            final.Debit_transaction_amount,
            final.Total_no_of_debit_transactions,
            final.Wash_Ratio,
            final.SEGMENT,
            final.RISK,
            final.SAR_FLAG
    from 
    (
        (
            select subquery.CUSTOMER_NUMBER_1 as CUSTOMER_NUMBER_main,
                    subquery.Credit_transaction_amount,
                    subquery.Total_no_of_credit_transactions,
                    case
                         when subquery.Debit_transaction_amount is NULL then 0
                         else Debit_transaction_amount
                    end as Debit_transaction_amount,
                    case
                         when subquery.Total_no_of_debit_transactions is NULL then 0
                         else Total_no_of_debit_transactions
                    end as Total_no_of_debit_transactions,
                    case
                         when subquery.Debit_transaction_amount = 0
                         or subquery.Debit_transaction_amount is NULL then 0
                         else subquery.Credit_transaction_amount / subquery.Debit_transaction_amount
                    end as Wash_Ratio
            from 
            (
                (
                    select customer_number as CUSTOMER_NUMBER_1, 
                            sum(transaction_amount) as Credit_transaction_amount, 
                            count(*) as Total_no_of_credit_transactions
                    from 
                    (
                        select * 
                        from {trans_data} as trans_table left join {acc_data} as acc_table
                        on trans_table.benef_account_number = acc_table.account_number
                    )
                    where account_number not in ('None')
                    group by 1
                ) credit left join
                (
                    select customer_number as CUSTOMER_NUMBER_2, 
                            sum(transaction_amount) as Debit_transaction_amount, 
                            count(*) as Total_no_of_debit_transactions
                    from 
                    (
                        select * 
                        from {trans_data} as trans_table left join {acc_data} as acc_table
                        on trans_table.orig_account_number = acc_table.account_number
                    )
                    where account_number not in ('None')
                    group by 1
                ) debit on credit.CUSTOMER_NUMBER_1 = debit.CUSTOMER_NUMBER_2 
            ) subquery
        ) main left join 
        (
            select subquery.CUSTOMER_NUMBER_3 as CUSTOMER_NUMBER_cust,
                    subquery.SEGMENT,
                    subquery.RISK,
                    case
                         when subquery.SAR_FLAG is NULL then 'N'
                         else subquery.SAR_FLAG
                    end as SAR_FLAG    
            from
            (
                (
                    select customer_number as CUSTOMER_NUMBER_3, 
                            business_segment as SEGMENT,
                            case
                                when RISK_CLASSIFICATION = 1 then 'Low Risk'
                                when RISK_CLASSIFICATION = 2 then 'Medium Risk'
                                when RISK_CLASSIFICATION = 3 then 'High Risk'
                                else 'Unknown Risk'
                            end AS RISK
                    from {cust_data}
                ) cd left join
                (
                    select customer_number as CUSTOMER_NUMBER_4, 
                            sar_flag as SAR_FLAG
                    from {alert_data}
                ) ad on cd.CUSTOMER_NUMBER_3 = ad.CUSTOMER_NUMBER_4
            ) subquery
        ) cust_alert on cust_alert.CUSTOMER_NUMBER_cust = main.CUSTOMER_NUMBER_main
    ) final
"""

In [8]:
from tms_data_interface import SQLQueryInterface

class Scenario:
    seq = SQLQueryInterface(schema="transactionschema")

    def logic(self, **kwargs):
        row_list = self.seq.execute_raw(query.format(trans_data="transaction10m",
                                                    cust_data="customer_data_v1",
                                                    acc_data="account_data_v1",
                                                    alert_data="alert_data_v1")
                                       )
        cols = ["Focal_id", "Credit_transaction_amount",
                "Total_no_of_credit_transactions",
                "Debit_transaction_amount", "Total_no_of_debit_transactions",
                "Wash_Ratio", "Segment", "Risk", "SAR_FLAG"]
        df = pd.DataFrame(row_list, columns = cols)
        return df

In [9]:
# sen = Scenario()
# sen.logic()

Focal_id  Credit_transaction_amount  Total_no_of_credit_transactions  \
0      PN808624               4.601504e+09                             3239   
1      PN663041               2.106224e+09                             1573   
2      PN525913               1.057799e+09                              776   
3      PN440274               4.806265e+09                             3506   
4      PN213026               3.982349e+09                             2809   
...         ...                        ...                              ...   
10009  PN774741               3.373466e+07                              250   
10010  PN868326               3.785344e+07                              259   
10011  PN667837               3.330357e+07                              256   
10012  PN809566               3.890076e+07                              276   
10013  PN739647               3.505184e+07                              223   

       Debit_transaction_amount  Total_no_of_debit_transactions  Wash_Ratio  \
0                  4.461280e+09                            3129    1.031431   
1                  2.281829e+09                            1563    0.923042   
2                  1.223876e+09                             850    0.864302   
3                  4.972813e+09                            3599    0.966508   
4                  4.122674e+09                            2783    0.965963   
...                         ...                             ...         ...   
10009              2.443148e+07                             381    1.380787   
10010              2.408309e+07                             352    1.571785   
10011              2.676301e+07                             359    1.244388   
10012              2.554121e+07                             400    1.523059   
10013              2.232980e+07                             381    1.569734   

                   Segment         Risk SAR_FLAG  
0        Corporate Banking  Medium Risk        N  
1        Corporate Banking     Low Risk        N  
2       Whole Sale Banking     Low Risk        N  
3       Whole Sale Banking  Medium Risk        N  
4       Whole Sale Banking  Medium Risk        N  
...                    ...          ...      ...  
10009     Priority Banking  Medium Risk        N  
10010  Ultra High NetWorth  Medium Risk        Y  
10011          Mass Market  Medium Risk        N  
10012               Others     Low Risk        N  
10013               Others     Low Risk        N  

[10014 rows x 9 columns]